# Importing libraries needed for this project

In [1]:
!conda update -c conda-forge -y pandas
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.21.0               |             py_0          58 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ------------------------------------------------------------
                                           Total:          92 KB

The following NEW packages will be INSTALLED:

    geographiclib: 1.50-py_0   conda-forge
    geopy:         1.21.0-py_0 conda-forge


geopy-1.21.0         | 58 KB     | ##################################### | 100% 
geographiclib-1.50   | 34 KB     | ##################################### | 100% 
Preparing transaction: done
Verifying transaction: done
Executi

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [4]:
#Transform this data of nested Python dictionaries into a *pandas* dataframe. 
#First, create an empty dataframe.

# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)
neighborhoods

Empty DataFrame
Columns: [Borough, Neighborhood, Latitude, Longitude]
Index: []

In [5]:
# Since all the relevant data is in the *features* key, a new variable that includes this data can be defined.
new_york_neighborhoods = newyork_data['features']
new_york_neighborhoods

[{'type': 'Feature',
  'id': 'nyu_2451_34572.1',
  'geometry': {'type': 'Point',
   'coordinates': [-73.84720052054902, 40.89470517661]},
  'geometry_name': 'geom',
  'properties': {'name': 'Wakefield',
   'stacked': 1,
   'annoline1': 'Wakefield',
   'annoline2': None,
   'annoline3': None,
   'annoangle': 0.0,
   'borough': 'Bronx',
   'bbox': [-73.84720052054902,
    40.89470517661,
    -73.84720052054902,
    40.89470517661]}},
 {'type': 'Feature',
  'id': 'nyu_2451_34572.2',
  'geometry': {'type': 'Point',
   'coordinates': [-73.82993910812398, 40.87429419303012]},
  'geometry_name': 'geom',
  'properties': {'name': 'Co-op City',
   'stacked': 2,
   'annoline1': 'Co-op',
   'annoline2': 'City',
   'annoline3': None,
   'annoangle': 0.0,
   'borough': 'Bronx',
   'bbox': [-73.82993910812398,
    40.87429419303012,
    -73.82993910812398,
    40.87429419303012]}},
 {'type': 'Feature',
  'id': 'nyu_2451_34572.3',
  'geometry': {'type': 'Point',
   'coordinates': [-73.82780644716412, 

In [6]:
#Loop through the data and fill the dataframe one row at a time.
for data in new_york_neighborhoods:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [7]:
# Use Foursquare API to explore the neighborhoods and segment them.
# Define Foursquare credentials

CLIENT_ID = 'JWF0SQO44XVRT3LGIMOU43XWIQHRZ1OB1XESZA21SN4BR4HR'
CLIENT_SECRET = '3AFUMIC0H5L0NZTL4DGJIKPAT5VWLKKWF3NQUFHUEGM0C3GT'
VERSION = '20180605'

In [8]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [9]:
# Code to run the above function on each neighborhood and create a new dataframe called "new_york_venues*.
new_york_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [10]:
# Create dataframe for Toronto
# Create a dataframe from Wikipedia page
# Scrape a Wikipedia page to obtain teh Toronto postal codes from the page

Toronto_neighborhoods=pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')
Toronto_postal_codes=Toronto_neighborhoods[0]
Toronto_postal_codes.head()

Postal Code           Borough               Neighborhood
0         M1A      Not assigned                        NaN
1         M2A      Not assigned                        NaN
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [11]:
# Ignore Not assigned burrows from Toronto_postal_code

Toronto_postal_codes['Borough'].replace('Not assigned', np.NaN, inplace=True)
Toronto_postal_codes.head()

Postal Code           Borough               Neighborhood
0         M1A               NaN                        NaN
1         M2A               NaN                        NaN
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [12]:
# Then, drop rows with missing values in the "Borough" column.

Toronto_postal_codes.dropna(subset=['Borough'], axis=0, inplace=True)
Toronto_postal_codes.reset_index(drop=True, inplace=True)
Toronto_postal_codes.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [13]:
# Incorporate latitude and longitude into the dataframe
# Data of latitude and longitude are already available for each postal code

Geo_neighborhoods_toronto=pd.read_csv('http://cocl.us/Geospatial_data')
Geo_neighborhoods_toronto.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [14]:
# Since there is a common column (Postal code), both dataframes can be joined into one.
# Column "Postal code" is duplicated, and one of them can be dropped now to obtain the final dataframe.

Toronto_data = pd.merge(left=Toronto_postal_codes, right=Geo_neighborhoods_toronto, left_on='Postal Code', right_on='Postal Code')
Toronto_data.drop('Postal Code', axis=1, inplace=True)
Toronto_data.head()

Borough                                 Neighborhood   Latitude  \
0        North York                                    Parkwoods  43.753259   
1        North York                             Victoria Village  43.725882   
2  Downtown Toronto                    Regent Park, Harbourfront  43.654260   
3        North York             Lawrence Manor, Lawrence Heights  43.718518   
4  Downtown Toronto  Queen's Park, Ontario Provincial Government  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

In [15]:
# Use Foursquare API to explore the neighborhoods of Toronto.
# The API credentials were already defined for New York
# getNearbyVenues code defined before will be used to create a new dataframe called "toronto_venues*.

toronto_venues = getNearbyVenues(names=Toronto_data['Neighborhood'],
                                   latitudes=Toronto_data['Latitude'],
                                   longitudes=Toronto_data['Longitude']
                                )

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmount Park
Bayview Village
Downsview
The Danforth West, Ri

In [16]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0         Parkwoods              43.753259              -79.329656   
1         Parkwoods              43.753259              -79.329656   
2         Parkwoods              43.753259              -79.329656   
3  Victoria Village              43.725882              -79.315572   
4  Victoria Village              43.725882              -79.315572   

                        Venue  Venue Latitude  Venue Longitude  \
0             Brookbanks Park       43.751976       -79.332140   
1               Variety Store       43.751974       -79.333114   
2  TTC stop - 44 Valley Woods       43.755402       -79.333741   
3      Victoria Village Arena       43.723481       -79.315635   
4                 Tim Hortons       43.725517       -79.313103   

      Venue Category  
0               Park  
1  Food & Drink Shop  
2           Bus Stop  
3       Hockey Arena  
4        Coffee Shop

In [17]:
new_york_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
2         Walgreens       40.896528       -73.844700        Pharmacy  
3          Rite Aid       40.896649       -73.844846        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [18]:
# Chech number of venues returned for each neighborhood in Toronto and NYC
# NYC

new_york_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      30                      30   
Annadale                                      12                      12   
Arden Heights                                  4                       4   
Arlington                                      5                       5   
Arrochar                                      20                      20   
Arverne                                       18                      18   
Astoria                                       30                      30   
Astoria Heights                               13                      13   
Auburndale                                    18                      18   
Bath Beach                                    30                      30   
Battery Park City                             30                      30   
Bay Ridge                                     30                      30   
Bay Terrace                                   39                      39   
Baychester                                    22                      22   
Bayside                                       30                      30   
Bayswater                                      2                       2   
Bedford Park                                  30                      30   
Bedford Stuyvesant                            27                      27   
Beechhurst                                    15                      15   
Bellaire                                      13                      13   
Belle Harbor                                  17                      17   
Bellerose                                     19                      19   
Belmont                                       30                      30   
Bensonhurst                                   26                      26   
Bergen Beach                                   7                       7   
Blissville                                    17                      17   
Bloomfield                                     5                       5   
Boerum Hill                                   30                      30   
Borough Park                                  18                      18   
Breezy Point                                   3                       3   
Briarwood                                     11                      11   
Brighton Beach                                30                      30   
Broad Channel                                  6                       6   
Broadway Junction                             16                      16   
Bronxdale                                     12                      12   
Brooklyn Heights                              30                      30   
Brookville                                     1                       1   
Brownsville                                   16                      16   
Bulls Head                                    30                      30   
Bushwick                                      30                      30   
Butler Manor                                   5                       5   
Cambria Heights                               14                      14   
Canarsie                                       7                       7   
Carnegie Hill                                 30                      30   
Carroll Gardens                               30                      30   
Castle Hill                                    7                       7   
Castleton Corners                             16                      16   
Central Harlem                                30                      30   
Charleston                                    29                      29   
Chelsea                                       38                      38   
Chinatown                                     30                      30   

In [19]:
# Toronto

toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               4   
Alderwood, Long Branch                                                 10   
Bathurst Manor, Wilson Heights, Downsview North                        19   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      22   
Berczy Park                                                            30   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           22   
Business reply mail Processing Centre                                  18   
CN Tower, King and Spadina, Railway Lands, Harb...                     16   
Caledonia-Fairbanks                                                     4   
Canada Post Gateway Processing Centre                                  12   
Cedarbrae                                                               8   
Central Bay Street                                                     30   
Christie                                                               17   
Church and Wellesley                                                   30   
Clarks Corners, Tam O'Shanter, Sullivan                                13   
Cliffside, Cliffcrest, Scarborough Village West                         2   
Commerce Court, Victoria Hotel                                         30   
Davisville                                                             30   
Davisville North                                                        7   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        5   
Don Mills                                                              26   
Dorset Park, Wexford Heights, Scarborough Town ...                      5   
Downsview                                                              16   
Dufferin, Dovercourt Village                                           19   
East Toronto                                                            4   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      7   
Fairview, Henry Farm, Oriole                                           30   
First Canadian Place, Underground city                                 30   
Forest Hill North & West                                                4   
Garden District, Ryerson                                               30   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                         9   
Guildwood, Morningside, West Hill                                       7   
Harbourfront East, Union Station, Toronto Islands                      30   
High Park, The Junction South                                          22   
Hillcrest Village                                                       6   
Humber Summit                                                           1   
Humberlea, Emery                                                        1   
Humewood-Cedarvale                                                      3   
India Bazaar, The Beaches West                                         22   
Kennedy Park, Ionview, East Birchmount Park                             7   
Kensington Market, Chinatown, Grange Park                              30   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                                       14   
Lawrence Park                                                           3   
Leaside                                                                30   
Little Portugal, Trinity                                               30   
Malvern, Rouge                                                          1   
Milliken, Agincourt North, Steeles East, L'Amor.

In [20]:
# Let's see the number of unique categories in each city

# NYC

print('There are {} uniques categories in New York City.'.format(len(new_york_venues['Venue Category'].unique())))
print('There are {} uniques categories in Toronto.'.format(len(toronto_venues['Venue Category'].unique())))

There are 384 uniques categories in New York City.
There are 230 uniques categories in Toronto.


In [21]:
# Analyze each neighborhood
# one hot encoding

# NYC

new_york_onehot = pd.get_dummies(new_york_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
new_york_onehot['Neighborhood'] = new_york_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [new_york_onehot.columns[-1]] + list(new_york_onehot.columns[:-1])
new_york_onehot = new_york_onehot[fixed_columns]

new_york_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Astrologer  Athletics & Sports  \
0                    0                 0           0                   0   
1                    0                 0           0                   0   
2                    0                 0           0                   0   
3                    0                 0           0                   0   
4                    0                 0           0                   0   

   Auditorium  Australian Restaurant  Austrian Restaurant  Auto Garage  \
0           0                      0                    0            0   
1           0                      0                    0            0   
2           0                      0                    0            0   
3           0                      0                    0            0   
4           0                      0                    0            0   

   Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0          0           0       0     0    0               0   
1                0          0           0       0     0    0               0   
2                0          0           0       0     0    0               0   
3                0          0           0       0     0    0               0   
4                0          0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Beach  Beach Bar  Bed & Breakfast  \
0                 0                 0      0          0                0   
1                 0                 0      0          0                0   
2                 0                 0      0          0                0   
3                 0                 0      0          0                0   
4                 0                 0      0          0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0   
4         0            0           0              0                         0   

   Bike Shop  Bike Trail  Bistro  Board Shop  Boarding House  Boat or Ferry  \
0          0           0       0           0               0              0   
1          0           0       0           0               0              0   
2          0           0       0           0               0              0   
3          0           0       0           0               0              0   
4     

In [22]:
# Toronto

toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Accessories Store  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0         0            0           0                    0                 0   
1         0            0           0                    0                 0   
2         0            0           0                    0                 0   
3         0            0           0                    0                 0   
4         0            0           0                    0                 0   

   Athletics & Sports  Auto Garage  Auto Workshop  BBQ Joint  Baby Store  \
0                   0            0              0          0           0   
1                   0            0              0          0           0   
2                   0            0              0          0           0   
3                   0            0              0          0           0   
4                   0            0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Basketball Stadium  \
0           0       0     0    0               0                   0   
1           0       0     0    0               0                   0   
2           0       0     0    0               0                   0   
3           0       0     0    0               0                   0   
4           0       0     0    0               0                   0   

   Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  Bistro  Board Shop  \
0         0           0                   0          0       0           0   
1         0           0                   0          0       0           0   
2         0           0                   0          0       0           0   
3         0           0                   0          0       0           0   
4         0           0                   0          0       0           0   

   Boat or Ferry  Bookstore  Boutique  Breakfast Spot  Brewery  Bridal Shop  \
0              0          0         0               0        0            0   
1              0          0         0               0        0            0   
2              0          0         0               0        0            0   
3              0          0         0               0        0            0   
4              0          0         0               0        0            0   

   Bubble Tea Shop  Burger Joint  Burrito Place  Bus Line  Bus Station  \
0                0             0              0         0            0   
1                0             0              0         0            0   
2                0             0              0         0            0   
3                0             0              0         0            0   
4                0             0              0         0            0   

   Bus Stop  Butcher  Cafeteria  Café  Cajun / Creole Restaurant  Candy Store  \
0         0        0          0     0                          0            0   
1         0        0          0     0                          0            0   
2         1        0          0     0                         

In [23]:
# Group rows by neighborhood and take the mean of occurrence for each category

# NYC
new_york_grouped = new_york_onehot.groupby('Neighborhood').mean().reset_index()
new_york_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.025641   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.000000           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.066667           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.066667           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.133333           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.033333           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.033333           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.033333           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.066667           0.000000   
59                  Co-op City     0.000000           0.00

In [24]:
# Toronto
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                           Agincourt     0.000000   
1                              Alderwood, Long Branch     0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North     0.000000   
3                                     Bayview Village     0.000000   
4                   Bedford Park, Lawrence Manor East     0.000000   
5                                         Berczy Park     0.000000   
6                         Birch Cliff, Cliffside West     0.000000   
7        Brockton, Parkdale Village, Exhibition Place     0.000000   
8               Business reply mail Processing Centre     0.055556   
9   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
10                                Caledonia-Fairbanks     0.000000   
11              Canada Post Gateway Processing Centre     0.000000   
12                                          Cedarbrae     0.000000   
13                                 Central Bay Street     0.033333   
14                                           Christie     0.000000   
15                               Church and Wellesley     0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan     0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West     0.000000   
18                     Commerce Court, Victoria Hotel     0.000000   
19                                         Davisville     0.000000   
20                                   Davisville North     0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn     0.000000   
22                                          Don Mills     0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...     0.000000   
24                                          Downsview     0.000000   
25                       Dufferin, Dovercourt Village     0.000000   
26                                       East Toronto     0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...     0.000000   
28                       Fairview, Henry Farm, Oriole     0.000000   
29             First Canadian Place, Underground city     0.000000   
30                           Forest Hill North & West     0.000000   
31                           Garden District, Ryerson     0.000000   
32                                          Glencairn     0.000000   
33                    Golden Mile, Clairlea, Oakridge     0.000000   
34                  Guildwood, Morningside, West Hill     0.000000   
35  Harbourfront East, Union Station, Toronto Islands     0.000000   
36                      High Park, The Junction South     0.000000   
37                                  Hillcrest Village     0.000000   
38                                      Humber Summit     0.000000   
39                                   Humberlea, Emery     0.000000   
40                                 Humewood-Cedarvale     0.000000   
41                     India Bazaar, The Beaches West     0.000000   
42        Kennedy Park, Ionview, East Birchmount Park     0.000000   
43          Kensington Market, Chinatown, Grange Park     0.000000   
44  Kingsview Village, St. Phillips, Martin Grove ...     0.000000   
45                   Lawrence Manor, Lawrence Heights     0.000000   
46                                      Lawrence Park     0.000000   
47                                            Leaside     0.000000   
48                           Little Portugal, Trinity     0.033333   
49                                     Malvern, Rouge     0.000000   
50  Milliken, Agincourt North, Steeles East, L'Amo...     0.000000   
51  Mimico NW, The Queensway West, South of Bloor,...     0.000000   
52                        Moore Park, Summerhill East     0.000000   
53       New Toronto, Mimico South, Humber Bay Shores     0.000000   
54           North Park, Maple Leaf Park, Upwood Park     0.000000   
55                                 North Toronto West     0.043478   
56                                          Northwe

In [25]:
print('The amount of neighborhoods in New York City is: ', new_york_grouped.shape[0])
print('The amount of neighborhoods in Toronto is: ', toronto_grouped.shape[0])

The amount of neighborhoods in New York City is:  300
The amount of neighborhoods in Toronto is:  96


In [26]:
# Most common venues

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

# NYC

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
new_york_venues_sorted = pd.DataFrame(columns=columns)
new_york_venues_sorted['Neighborhood'] = new_york_grouped['Neighborhood']

for ind in np.arange(new_york_grouped.shape[0]):
    new_york_venues_sorted.iloc[ind, 1:] = return_most_common_venues(new_york_grouped.iloc[ind, :], num_top_venues)

new_york_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place         Deli / Bodega   
1       Annadale   American Restaurant                   Pub   
2  Arden Heights              Pharmacy           Coffee Shop   
3      Arlington         Deli / Bodega   American Restaurant   
4       Arrochar           Pizza Place         Deli / Bodega   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    Chinese Restaurant           Supermarket              Pharmacy   
1         Deli / Bodega           Pizza Place                 Diner   
2              Bus Stop           Pizza Place         Women's Store   
3         Grocery Store         Boat or Ferry              Bus Stop   
4    Italian Restaurant              Bus Stop        Cosmetics Shop   

      6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0         Electronics Store                 Bakery  Fast Food Restaurant   
1                Restaurant          Train Station              Pharmacy   
2                      Farm  Entertainment Service  Ethiopian Restaurant   
3             Women's Store                  Field         Event Service   
4  Mediterranean Restaurant    Sporting Goods Shop        Sandwich Place   

  9th Most Common Venue     10th Most Common Venue  
0         Grocery Store          Martial Arts Dojo  
1                  Park                 Sports Bar  
2         Event Service                Event Space  
3           Event Space                    Exhibit  
4            Bagel Shop  Middle Eastern Restaurant

In [27]:
# Toronto

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
toronto_venues_sorted = pd.DataFrame(columns=columns)
toronto_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    toronto_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

toronto_venues_sorted.head()

Neighborhood      1st Most Common Venue  \
0                                        Agincourt  Latin American Restaurant   
1                           Alderwood, Long Branch                Pizza Place   
2  Bathurst Manor, Wilson Heights, Downsview North                Coffee Shop   
3                                  Bayview Village        Japanese Restaurant   
4                Bedford Park, Lawrence Manor East                Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0          Skating Rink                Lounge        Breakfast Spot   
1           Coffee Shop        Sandwich Place          Dance Studio   
2                  Bank           Pizza Place                 Diner   
3    Chinese Restaurant                  Bank                  Café   
4        Sandwich Place            Restaurant    Italian Restaurant   

  5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
0         Deli / Bodega             Drugstore                   Donut Shop   
1          Skating Rink              Pharmacy                          Gym   
2        Sandwich Place           Bridal Shop                Deli / Bodega   
3         Women's Store         Deli / Bodega  Eastern European Restaurant   
4      Greek Restaurant       Thai Restaurant                      Butcher   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0               Dog Run   Distribution Center         Discount Store  
1                   Pub                  Pool          Deli / Bodega  
2            Restaurant        Ice Cream Shop       Sushi Restaurant  
3             Drugstore            Donut Shop                Dog Run  
4                   Pub      Sushi Restaurant                   Café

In [28]:
# Cluster neighborhoods

# set number of clusters
kclusters = 10

# NYC

new_york_grouped_clustering = new_york_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans_NYC = KMeans(n_clusters=kclusters, random_state=0).fit(new_york_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans_NYC.labels_[0:10] 

array([3, 3, 9, 9, 3, 1, 4, 3, 4, 1], dtype=int32)

In [29]:
# Toronto

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans_TOR = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans_TOR.labels_[0:10] 

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [30]:
# add clustering labels
new_york_venues_sorted.insert(0, 'Cluster Labels', kmeans_NYC.labels_)

new_york_merged = neighborhoods

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
new_york_merged = new_york_merged.join(new_york_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

new_york_merged.head() # check the last columns!

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             1.0   
1   Bronx   Co-op City  40.874294 -73.829939             0.0   
2   Bronx  Eastchester  40.887556 -73.827806             0.0   
3   Bronx    Fieldston  40.895437 -73.905643             0.0   
4   Bronx    Riverdale  40.890834 -73.912585             0.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy            Laundromat                  Food   
1  Fast Food Restaurant           Bus Station         Grocery Store   
2           Bus Station  Caribbean Restaurant         Deli / Bodega   
3                 River           Bus Station                 Plaza   
4           Bus Station                  Park                  Bank   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Ice Cream Shop          Dessert Shop           Gas Station   
1              Pharmacy           Pizza Place            Bagel Shop   
2              Bus Stop                 Diner        Cosmetics Shop   
3      Business Service         Women's Store        Farmers Market   
4            Food Truck                   Gym            Playground   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0             Donut Shop        Sandwich Place         Women's Store   
1         Discount Store            Restaurant          Liquor Store   
2             Donut Shop         Bowling Alley  Fast Food Restaurant   
3  Entertainment Service  Ethiopian Restaurant         Event Service   
4                  Plaza          Home Service        Baseball Field   

  10th Most Common Venue  
0  Entertainment Service  
1         Baseball Field  
2          Metro Station  
3            Event Space  
4    Filipino Restaurant

In [31]:
# add clustering labels
toronto_venues_sorted.insert(0, 'Cluster Labels', kmeans_TOR.labels_)

toronto_merged = Toronto_data

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(toronto_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Borough                                 Neighborhood   Latitude  \
0        North York                                    Parkwoods  43.753259   
1        North York                             Victoria Village  43.725882   
2  Downtown Toronto                    Regent Park, Harbourfront  43.654260   
3        North York             Lawrence Manor, Lawrence Heights  43.718518   
4  Downtown Toronto  Queen's Park, Ontario Provincial Government  43.662301   

   Longitude  Cluster Labels 1st Most Common Venue  2nd Most Common Venue  \
0 -79.329656             3.0              Bus Stop                   Park   
1 -79.315572             0.0           Coffee Shop  Portuguese Restaurant   
2 -79.360636             0.0           Coffee Shop                   Park   
3 -79.464763             0.0        Clothing Store      Accessories Store   
4 -79.389494             0.0           Coffee Shop       Sushi Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0     Food & Drink Shop         Women's Store             Drugstore   
1          Hockey Arena     French Restaurant  Colombian Restaurant   
2        Breakfast Spot               Theater                Bakery   
3           Coffee Shop            Shoe Store   Arts & Crafts Store   
4    Mexican Restaurant              Beer Bar        Sandwich Place   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0               Donut Shop               Dog Run   Distribution Center   
1  Comfort Food Restaurant             Drugstore            Donut Shop   
2              Yoga Studio            Restaurant                   Pub   
3   Furniture / Home Store    Miscellaneous Shop              Boutique   
4             Burger Joint         Burrito Place                  Café   

   9th Most Common Venue 10th Most Common Venue  
0         Discount Store                  Diner  
1                Dog Run    Distribution Center  
2                   Café         Chocolate Shop  
3  Vietnamese Restaurant            Event Space  
4                   Park               Creperie

In [32]:
# Use geopy library to obtain latitude and longitude of New York City
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [33]:
# Remove data where missing values were found. Drop entire rows.

new_york_merged.dropna(subset=['Cluster Labels'], axis=0, inplace=True)
new_york_merged.head()

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201             1.0   
1   Bronx   Co-op City  40.874294 -73.829939             0.0   
2   Bronx  Eastchester  40.887556 -73.827806             0.0   
3   Bronx    Fieldston  40.895437 -73.905643             0.0   
4   Bronx    Riverdale  40.890834 -73.912585             0.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy            Laundromat                  Food   
1  Fast Food Restaurant           Bus Station         Grocery Store   
2           Bus Station  Caribbean Restaurant         Deli / Bodega   
3                 River           Bus Station                 Plaza   
4           Bus Station                  Park                  Bank   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Ice Cream Shop          Dessert Shop           Gas Station   
1              Pharmacy           Pizza Place            Bagel Shop   
2              Bus Stop                 Diner        Cosmetics Shop   
3      Business Service         Women's Store        Farmers Market   
4            Food Truck                   Gym            Playground   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0             Donut Shop        Sandwich Place         Women's Store   
1         Discount Store            Restaurant          Liquor Store   
2             Donut Shop         Bowling Alley  Fast Food Restaurant   
3  Entertainment Service  Ethiopian Restaurant         Event Service   
4                  Plaza          Home Service        Baseball Field   

  10th Most Common Venue  
0  Entertainment Service  
1         Baseball Field  
2          Metro Station  
3            Event Space  
4    Filipino Restaurant

In [34]:
# Change data type in Cluster Labels to integer. Code doesn't work with float.

new_york_merged['Cluster Labels']=new_york_merged['Cluster Labels'].astype('int')
new_york_merged.head()

Borough Neighborhood   Latitude  Longitude  Cluster Labels  \
0   Bronx    Wakefield  40.894705 -73.847201               1   
1   Bronx   Co-op City  40.874294 -73.829939               0   
2   Bronx  Eastchester  40.887556 -73.827806               0   
3   Bronx    Fieldston  40.895437 -73.905643               0   
4   Bronx    Riverdale  40.890834 -73.912585               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0              Pharmacy            Laundromat                  Food   
1  Fast Food Restaurant           Bus Station         Grocery Store   
2           Bus Station  Caribbean Restaurant         Deli / Bodega   
3                 River           Bus Station                 Plaza   
4           Bus Station                  Park                  Bank   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0        Ice Cream Shop          Dessert Shop           Gas Station   
1              Pharmacy           Pizza Place            Bagel Shop   
2              Bus Stop                 Diner        Cosmetics Shop   
3      Business Service         Women's Store        Farmers Market   
4            Food Truck                   Gym            Playground   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0             Donut Shop        Sandwich Place         Women's Store   
1         Discount Store            Restaurant          Liquor Store   
2             Donut Shop         Bowling Alley  Fast Food Restaurant   
3  Entertainment Service  Ethiopian Restaurant         Event Service   
4                  Plaza          Home Service        Baseball Field   

  10th Most Common Venue  
0  Entertainment Service  
1         Baseball Field  
2          Metro Station  
3            Event Space  
4    Filipino Restaurant

In [35]:
# create map of New York City with neighborhoods supoeimposed on top

map_clusters_NYC = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(new_york_merged['Latitude'], new_york_merged['Longitude'], new_york_merged['Neighborhood'], new_york_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_NYC)
       
map_clusters_NYC

In [36]:
# Use geopy library to obtain latitude and longitude of Toronto

address = 'Toronto, ON'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Toronto are 43.6534817, -79.3839347.


In [37]:
# Remove data where missing values were found. Drop entire rows.

toronto_merged.dropna(subset=['Cluster Labels'], axis=0, inplace=True)
toronto_merged.head()

Borough                                 Neighborhood   Latitude  \
0        North York                                    Parkwoods  43.753259   
1        North York                             Victoria Village  43.725882   
2  Downtown Toronto                    Regent Park, Harbourfront  43.654260   
3        North York             Lawrence Manor, Lawrence Heights  43.718518   
4  Downtown Toronto  Queen's Park, Ontario Provincial Government  43.662301   

   Longitude  Cluster Labels 1st Most Common Venue  2nd Most Common Venue  \
0 -79.329656             3.0              Bus Stop                   Park   
1 -79.315572             0.0           Coffee Shop  Portuguese Restaurant   
2 -79.360636             0.0           Coffee Shop                   Park   
3 -79.464763             0.0        Clothing Store      Accessories Store   
4 -79.389494             0.0           Coffee Shop       Sushi Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0     Food & Drink Shop         Women's Store             Drugstore   
1          Hockey Arena     French Restaurant  Colombian Restaurant   
2        Breakfast Spot               Theater                Bakery   
3           Coffee Shop            Shoe Store   Arts & Crafts Store   
4    Mexican Restaurant              Beer Bar        Sandwich Place   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0               Donut Shop               Dog Run   Distribution Center   
1  Comfort Food Restaurant             Drugstore            Donut Shop   
2              Yoga Studio            Restaurant                   Pub   
3   Furniture / Home Store    Miscellaneous Shop              Boutique   
4             Burger Joint         Burrito Place                  Café   

   9th Most Common Venue 10th Most Common Venue  
0         Discount Store                  Diner  
1                Dog Run    Distribution Center  
2                   Café         Chocolate Shop  
3  Vietnamese Restaurant            Event Space  
4                   Park               Creperie

In [38]:
# Change data type in Cluster Labels to integer. Code doesn't work with float.

toronto_merged['Cluster Labels']=toronto_merged['Cluster Labels'].astype('int')
toronto_merged.head()

Borough                                 Neighborhood   Latitude  \
0        North York                                    Parkwoods  43.753259   
1        North York                             Victoria Village  43.725882   
2  Downtown Toronto                    Regent Park, Harbourfront  43.654260   
3        North York             Lawrence Manor, Lawrence Heights  43.718518   
4  Downtown Toronto  Queen's Park, Ontario Provincial Government  43.662301   

   Longitude  Cluster Labels 1st Most Common Venue  2nd Most Common Venue  \
0 -79.329656               3              Bus Stop                   Park   
1 -79.315572               0           Coffee Shop  Portuguese Restaurant   
2 -79.360636               0           Coffee Shop                   Park   
3 -79.464763               0        Clothing Store      Accessories Store   
4 -79.389494               0           Coffee Shop       Sushi Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0     Food & Drink Shop         Women's Store             Drugstore   
1          Hockey Arena     French Restaurant  Colombian Restaurant   
2        Breakfast Spot               Theater                Bakery   
3           Coffee Shop            Shoe Store   Arts & Crafts Store   
4    Mexican Restaurant              Beer Bar        Sandwich Place   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0               Donut Shop               Dog Run   Distribution Center   
1  Comfort Food Restaurant             Drugstore            Donut Shop   
2              Yoga Studio            Restaurant                   Pub   
3   Furniture / Home Store    Miscellaneous Shop              Boutique   
4             Burger Joint         Burrito Place                  Café   

   9th Most Common Venue 10th Most Common Venue  
0         Discount Store                  Diner  
1                Dog Run    Distribution Center  
2                   Café         Chocolate Shop  
3  Vietnamese Restaurant            Event Space  
4                   Park               Creperie

In [39]:
# create map
map_clusters_TOR = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters_TOR)
       
map_clusters_TOR

In [40]:
# Examine each Cluster for venues in the buroughs of New York City

# Cluster 1

new_york_merged.loc[new_york_merged['Cluster Labels'] == 0, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough         Neighborhood 1st Most Common Venue  \
1            Bronx           Co-op City  Fast Food Restaurant   
2            Bronx          Eastchester           Bus Station   
3            Bronx            Fieldston                 River   
4            Bronx            Riverdale           Bus Station   
18           Bronx           West Farms           Bus Station   
85        Brooklyn             Sea Gate          Home Service   
158         Queens        Fresh Meadows           Bus Station   
159         Queens            Briarwood    Mexican Restaurant   
164         Queens        South Jamaica           Bus Station   
167         Queens  Springfield Gardens            Donut Shop   
169         Queens             Rosedale           Bus Station   
171         Queens        Broad Channel              Dive Bar   
183         Queens      Jamaica Estates          Intersection   
212  Staten Island              Oakwood            Playground   
267          Bronx    Claremont Village           Bus Station   
278         Queens           Blissville            Donut Shop   

             2nd Most Common Venue 3rd Most Common Venue  \
1                      Bus Station         Grocery Store   
2             Caribbean Restaurant         Deli / Bodega   
3                      Bus Station                 Plaza   
4                             Park                  Bank   
18                      Donut Shop           Coffee Shop   
85                           Beach                   Spa   
158                       Pharmacy    Chinese Restaurant   
159            Arts & Crafts Store  Fast Food Restaurant   
164  Vegetarian / Vegan Restaurant                Bakery   
167            Fried Chicken Joint           Bus Station   
169             Chinese Restaurant            Smoke Shop   
171                  Deli / Bodega   Sporting Goods Shop   
183              Indian Restaurant          Antique Shop   
212                    Bus Station                Lawyer   
267             Chinese Restaurant         Deli / Bodega   
278                  Deli / Bodega           Bus Station   

    4th Most Common Venue          5th Most Common Venue  \
1                Pharmacy                    Pizza Place   
2                Bus Stop                          Diner   
3        Business Service                  Women's Store   
4              Food Truck                            Gym   
18                   Park               Basketball Court   
85            Bus Station                    Video Store   
158        Cosmetics Shop  Vegetarian / Vegan Restaurant   
159         Deli / Bodega              Indian Restaurant   
164           Supermarket                  Grocery Store   
167          Intersection               Business Service   
169              Pharmacy                 Sandwich Place   
171       Other Nightlife                    Bus Station   
183           Bus Station                          Field   
212                   Bar                 Farmers Market   
267         Grocery Store                    Pizza Place   
278                   Bar                          Hotel   

     6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
1               Bagel Shop         Discount Store            Restaurant   
2           Cosmetics Shop             Donut Shop         Bowling Alley   
3           Farmers Market  Entertainment Service  Ethiopian Restaurant   
4               Playground                  Plaza          Home Service   
18                     Gym                 Lounge                  Bank   
85           Women's Store  Entertainment Service  Ethiopian Restaurant   
158             Playground            Pizza Place            Shoe Store   
159      Convenience Store                    Gym           Coffee Shop   
164   Caribbean Restaurant               Bus Line        Sandwich Place   
167   Fast Food Restaurant  Check Cashing Service            Shoe Store   
169           Liquor Store   Caribbean

In [41]:
# Cluster 2

new_york_merged.loc[new_york_merged['Cluster Labels'] == 1, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough          Neighborhood 1st Most Common Venue  \
0            Bronx             Wakefield              Pharmacy   
5            Bronx           Kingsbridge    Mexican Restaurant   
6        Manhattan           Marble Hill        Sandwich Place   
10           Bronx            Baychester        Discount Store   
16           Bronx               Fordham        Clothing Store   
21           Bronx            Mott Haven                   Gym   
23           Bronx              Longwood           Pizza Place   
25           Bronx            Morrisania           Bus Station   
29           Bronx          Country Club        Sandwich Place   
31           Bronx    Westchester Square  Fast Food Restaurant   
35           Bronx        Spuyten Duyvil                  Park   
37           Bronx            Pelham Bay    Italian Restaurant   
38           Bronx         Schuylerville           Pizza Place   
40           Bronx           Castle Hill                  Bank   
41           Bronx             Olinville  Caribbean Restaurant   
43           Bronx             Concourse         Grocery Store   
44           Bronx             Unionport        Ice Cream Shop   
47        Brooklyn           Bensonhurst      Sushi Restaurant   
48        Brooklyn           Sunset Park                  Bank   
51        Brooklyn        Brighton Beach            Restaurant   
54        Brooklyn              Flatbush           Coffee Shop   
56        Brooklyn         East Flatbush                  Park   
71        Brooklyn         Cypress Hills   Fried Chicken Joint   
73        Brooklyn         Starrett City            Donut Shop   
74        Brooklyn              Canarsie      Asian Restaurant   
75        Brooklyn             Flatlands              Pharmacy   
78        Brooklyn          Coney Island      Baseball Stadium   
79        Brooklyn            Bath Beach              Pharmacy   
90        Brooklyn             City Line            Donut Shop   
91        Brooklyn          Bergen Beach       Harbor / Marina   
93        Brooklyn   Prospect Park South  Caribbean Restaurant   
94        Brooklyn            Georgetown                  Bank   
133         Queens          Howard Beach    Italian Restaurant   
137         Queens         Richmond Hill           Pizza Place   
141         Queens         East Elmhurst            Donut Shop   
146         Queens             Woodhaven         Deli / Bodega   
147         Queens            Ozone Park                  Bank   
153         Queens           Little Neck    Italian Restaurant   
155         Queens             Glen Oaks              Pharmacy   
160         Queens        Jamaica Center     Mobile Phone Shop   
161         Queens       Oakland Gardens     Korean Restaurant   
162         Queens        Queens Village                  Bank   
163         Queens                Hollis                  Park   
165         Queens            St. Albans  Caribbean Restaurant   
166         Queens              Rochdale                Market   
168         Queens       Cambria Heights  Caribbean Restaurant   
175         Queens           Bay Terrace        Clothing Store   
177         Queens               Arverne             Surf Spot   
182         Queens            Holliswood           Supermarket   
185         Queens             Hillcrest         Grocery Store   
188         Queens             Laurelton  Caribbean Restaurant   
189         Queens           Lefrak City      Department Store   
190         Queens          Belle Harbor                 Beach   
191         Queens         Rockaway Park                 Beach   
196         Queens  Forest Hills Gardens         Grocery Store   
199  Staten Island             Stapleton                   Bar   
200  Staten Island              Rosebank    Mexican Restaurant   
216  Staten Island               Woodrow              Pharmacy   
221       Brooklyn           Ditmas Park           Pizza Place   
222       Brooklyn               Wingate   Fried Ch

In [42]:
# Cluster 3

new_york_merged.loc[new_york_merged['Cluster Labels'] == 2, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
76  Brooklyn  Mill Island                  Pool         Women's Store   

   3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
76  Fast Food Restaurant  Entertainment Service  Ethiopian Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
76         Event Service           Event Space               Exhibit   

   9th Most Common Venue 10th Most Common Venue  
76               Factory     Falafel Restaurant

In [43]:
# Cluster 4

new_york_merged.loc[new_york_merged['Cluster Labels'] == 3, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough         Neighborhood    1st Most Common Venue  \
7            Bronx             Woodlawn            Deli / Bodega   
8            Bronx              Norwood              Pizza Place   
11           Bronx       Pelham Parkway       Chinese Restaurant   
13           Bronx         Bedford Park                    Diner   
14           Bronx   University Heights              Pizza Place   
15           Bronx       Morris Heights       Chinese Restaurant   
17           Bronx         East Tremont              Pizza Place   
19           Bronx         High  Bridge                 Pharmacy   
20           Bronx              Melrose              Pizza Place   
24           Bronx          Hunts Point                     Bank   
26           Bronx            Soundview       Chinese Restaurant   
30           Bronx          Parkchester              Pizza Place   
33           Bronx          Morris Park              Pizza Place   
34           Bronx              Belmont       Italian Restaurant   
36           Bronx      North Riverdale              Pizza Place   
39           Bronx       Edgewater Park       Italian Restaurant   
42           Bronx       Pelham Gardens              Pizza Place   
45           Bronx             Edenwald              Supermarket   
46        Brooklyn            Bay Ridge                      Spa   
50        Brooklyn            Gravesend       Chinese Restaurant   
53        Brooklyn    Manhattan Terrace              Pizza Place   
55        Brooklyn        Crown Heights              Pizza Place   
60        Brooklyn          Brownsville               Restaurant   
80        Brooklyn         Borough Park                     Bank   
83        Brooklyn          Marine Park         Basketball Court   
89        Brooklyn           Ocean Hill            Deli / Bodega   
92        Brooklyn              Midwood              Pizza Place   
134         Queens               Corona       Mexican Restaurant   
135         Queens         Forest Hills     Gym / Fitness Center   
136         Queens          Kew Gardens           Cosmetics Shop   
140         Queens            Sunnyside              Pizza Place   
142         Queens              Maspeth                    Diner   
144         Queens             Glendale                  Brewery   
145         Queens            Rego Park                   Bakery   
149         Queens        College Point              Pizza Place   
154         Queens           Douglaston              Pizza Place   
156         Queens            Bellerose              Pizza Place   
157         Queens    Kew Gardens Hills                     Bank   
170         Queens         Far Rockaway       Chinese Restaurant   
174         Queens           Beechhurst       Chinese Restaurant   
176         Queens             Edgemere            Metro Station   
181         Queens          Floral Park         Basketball Court   
184         Queens      Queensboro Hill       Chinese Restaurant   
187         Queens           Lindenwood  Fruit & Vegetable Store   
194         Queens             Bellaire       Chinese Restaurant   
208  Staten Island    Castleton Corners              Pizza Place   
209  Staten Island      New Springville       Chinese Restaurant   
211  Staten Island             New Dorp       Italian Restaurant   
213  Staten Island          Great Kills       Italian Restaurant   
214  Staten Island          Eltingville         Sushi Restaurant   
215  Staten Island             Annadale      American Restaurant   
218  Staten Island        Tompkinsville   Thrift / Vintage Store   
220  Staten Island            Sunnyside              Pizza Place   
228  Staten Island             Arrochar              Pizza Place   
231  Staten Island         Dongan Hills                 Pharmacy   
232  Staten Island        Midland Beach                    Beach   
233  Staten Island           Grant City     Fast Food Restaurant   
240  Staten Island            Rossville              Pizza Place   

In [44]:
# Cluster 5

new_york_merged.loc[new_york_merged['Cluster Labels'] == 4, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough               Neighborhood      1st Most Common Venue  \
9            Bronx             Williamsbridge                        Bar   
12           Bronx                City Island            Harbor / Marina   
22           Bronx                Port Morris     Furniture / Home Store   
28           Bronx                Throgs Neck              Deli / Bodega   
49        Brooklyn                 Greenpoint                        Bar   
52        Brooklyn             Sheepshead Bay               Dessert Shop   
57        Brooklyn                 Kensington            Thai Restaurant   
58        Brooklyn            Windsor Terrace              Deli / Bodega   
59        Brooklyn           Prospect Heights                        Bar   
61        Brooklyn               Williamsburg                Coffee Shop   
62        Brooklyn                   Bushwick                        Bar   
63        Brooklyn         Bedford Stuyvesant              Deli / Bodega   
64        Brooklyn           Brooklyn Heights                Yoga Studio   
65        Brooklyn                Cobble Hill         Italian Restaurant   
66        Brooklyn            Carroll Gardens         Italian Restaurant   
67        Brooklyn                   Red Hook         Seafood Restaurant   
68        Brooklyn                    Gowanus         Italian Restaurant   
69        Brooklyn                Fort Greene               Cocktail Bar   
70        Brooklyn                 Park Slope                Coffee Shop   
81        Brooklyn              Dyker Heights                       Park   
82        Brooklyn            Gerritsen Beach                        Bar   
84        Brooklyn               Clinton Hill                  Wine Shop   
86        Brooklyn                   Downtown              Grocery Store   
87        Brooklyn                Boerum Hill     Furniture / Home Store   
88        Brooklyn  Prospect Lefferts Gardens                       Café   
95        Brooklyn          East Williamsburg                        Bar   
96        Brooklyn                 North Side                Yoga Studio   
97        Brooklyn                 South Side                Pizza Place   
98        Brooklyn              Ocean Parkway           Sushi Restaurant   
99        Brooklyn              Fort Hamilton       Gym / Fitness Center   
100      Manhattan                  Chinatown         Chinese Restaurant   
101      Manhattan         Washington Heights                       Café   
102      Manhattan                     Inwood         Frozen Yogurt Shop   
103      Manhattan           Hamilton Heights                Coffee Shop   
104      Manhattan             Manhattanville         Seafood Restaurant   
105      Manhattan             Central Harlem                        Bar   
106      Manhattan                East Harlem         Mexican Restaurant   
107      Manhattan            Upper East Side       Gym / Fitness Center   
108      Manhattan                  Yorkville                  Wine Shop   
109      Manhattan                 Lenox Hill                        Gym   
110      Manhattan           Roosevelt Island                       Park   
111      Manhattan            Upper West Side         Seafood Restaurant   
112      Manhattan             Lincoln Square                    Theater   
113      Manhattan                    Clinton                    Theater   
114      Manhattan                    Midtown             Clothing Store   
115      Manhattan                Murray Hill          Korean Restaurant   
116      Manhattan                    Chelsea             Ice Cream Shop   
117      Manhattan          Greenwich Village         Italian Restaurant   
118      Manhattan               East Village      Vietnamese Restaurant   
119      Manhattan            Lower East Side                Art Gallery   
120      Manhattan                    Tribeca           Greek Restaurant   
121      Manhattan               Little Italy              

In [45]:
# Cluster 6

new_york_merged.loc[new_york_merged['Cluster Labels'] == 5, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough      Neighborhood 1st Most Common Venue  \
32           Bronx          Van Nest           Pizza Place   
72        Brooklyn     East New York         Deli / Bodega   
148         Queens  South Ozone Park                  Park   
150         Queens        Whitestone       Bubble Tea Shop   
193         Queens        Brookville         Deli / Bodega   
195         Queens      North Corona         Deli / Bodega   
205  Staten Island     Port Richmond   Rental Car Location   
264         Queens            Utopia         Deli / Bodega   

    2nd Most Common Venue      3rd Most Common Venue  4th Most Common Venue  \
32          Deli / Bodega                 Hookah Bar            Supermarket   
72     Spanish Restaurant                Pizza Place                    Gym   
148         Deli / Bodega                        Bar   Fast Food Restaurant   
150          Dance Studio              Deli / Bodega            Candy Store   
193         Women's Store       Fast Food Restaurant  Entertainment Service   
195           Pizza Place                      Hotel   Gym / Fitness Center   
205      Basketball Court              Deli / Bodega               Bus Stop   
264             Locksmith  South American Restaurant       Basketball Court   

         5th Most Common Venue      6th Most Common Venue  \
32   Middle Eastern Restaurant                Bus Station   
72        Caribbean Restaurant          Convenience Store   
148                 Food Truck                 Donut Shop   
150              Historic Site              Women's Store   
193       Ethiopian Restaurant              Event Service   
195                     Bakery  South American Restaurant   
205                 Donut Shop              Women's Store   
264                     Bakery            Automotive Shop   

         7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
32                  Donut Shop           Coffee Shop        Farmers Market   
72         Fried Chicken Joint         Event Service         Metro Station   
148                      Hotel        Sandwich Place    Falafel Restaurant   
150       Fast Food Restaurant         Event Service           Event Space   
193                Event Space               Exhibit               Factory   
195  Latin American Restaurant     Mobile Phone Shop  Fast Food Restaurant   
205       Fast Food Restaurant         Event Service           Event Space   
264                 Donut Shop           Pizza Place            Playground   

    10th Most Common Venue  
32           Event Service  
72                   Plaza  
148  Entertainment Service  
150                Exhibit  
193     Falafel Restaurant  
195                 Museum  
205                Exhibit  
264         History Museum

In [46]:
# Cluster 7

new_york_merged.loc[new_york_merged['Cluster Labels'] == 6, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
207  Staten Island   Port Ivory      Business Service              Creperie   

     3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
207  Entertainment Service  Ethiopian Restaurant         Event Service   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
207           Event Space               Exhibit               Factory   

    9th Most Common Venue 10th Most Common Venue  
207    Falafel Restaurant                   Farm

In [47]:
# Cluster 8

new_york_merged.loc[new_york_merged['Cluster Labels'] == 7, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
179  Queens     Neponsit                 Beach         Women's Store   

    3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
179     French Restaurant  Entertainment Service  Ethiopian Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
179         Event Service           Event Space               Exhibit   

    9th Most Common Venue 10th Most Common Venue  
179               Factory     Falafel Restaurant

In [48]:
# Cluster 9

new_york_merged.loc[new_york_merged['Cluster Labels'] == 8, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
192         Queens   Somerville                  Park         Women's Store   
203  Staten Island    Todt Hill                  Park         Women's Store   

    3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
192             Irish Pub  Entertainment Service  Ethiopian Restaurant   
203             Irish Pub  Entertainment Service  Ethiopian Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192         Event Service           Event Space               Exhibit   
203         Event Service           Event Space               Exhibit   

    9th Most Common Venue 10th Most Common Venue  
192               Factory     Falafel Restaurant  
203               Factory     Falafel Restaurant

In [49]:
# Cluster 10

new_york_merged.loc[new_york_merged['Cluster Labels'] == 9, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough      Neighborhood 1st Most Common Venue  \
27           Bronx      Clason Point                  Park   
77        Brooklyn   Manhattan Beach                  Café   
198  Staten Island      New Brighton              Bus Stop   
202  Staten Island       Grymes Hill               Dog Run   
204  Staten Island       South Beach                  Pier   
206  Staten Island  Mariner's Harbor    Italian Restaurant   
217  Staten Island       Tottenville        Cosmetics Shop   
224  Staten Island         Park Hill              Bus Stop   
226  Staten Island      Graniteville         Grocery Store   
227  Staten Island         Arlington         Deli / Bodega   
241  Staten Island     Arden Heights              Pharmacy   
245  Staten Island        Bloomfield        Discount Store   
256  Staten Island     Randall Manor              Bus Stop   
258  Staten Island          Elm Park              Bus Stop   
285  Staten Island       Willowbrook    Chinese Restaurant   
303         Queens         Bayswater                  Park   
305  Staten Island         Fox Hills              Bus Stop   

      2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
27            Grocery Store                  Pool         Boat or Ferry   
77                 Bus Stop           Pizza Place                 Beach   
198           Deli / Bodega                  Park         Bowling Alley   
202                Bus Stop         Women's Store  Fast Food Restaurant   
204           Deli / Bodega                 Beach              Bus Stop   
206           Deli / Bodega              Bus Stop     Other Repair Shop   
217  Thrift / Vintage Store    Italian Restaurant         Deli / Bodega   
224      Athletics & Sports  Gym / Fitness Center           Coffee Shop   
226           Boat or Ferry              Bus Stop        Sandwich Place   
227     American Restaurant         Grocery Store         Boat or Ferry   
241             Coffee Shop              Bus Stop           Pizza Place   
245       Recreation Center            Theme Park              Bus Stop   
256              Playground            Bagel Shop                  Park   
258      Italian Restaurant            Toll Plaza   American Restaurant   
285                Bus Stop            Bagel Shop           Pizza Place   
303              Playground         Women's Store   Empanada Restaurant   
305               BBQ Joint         Grocery Store        Sandwich Place   

     5th Most Common Venue      6th Most Common Venue  7th Most Common Venue  \
27                Bus Stop  South American Restaurant         Farmers Market   
77                    Food             Ice Cream Shop             Playground   
198         Discount Store                 Playground          Women's Store   
202   Ethiopian Restaurant              Event Service            Event Space   
204     Athletics & Sports              Women's Store   Fast Food Restaurant   
206     Athletics & Sports              Women's Store   Ethiopian Restaurant   
217     Mexican Restaurant                   Bus Stop   Fast Food Restaurant   
224                  Hotel              Women's Store         Farmers Market   
226          Women's Store             Farmers Market   Ethiopian Restaurant   
227               Bus Stop              Women's Store                  Field   
241          Women's Store                       Farm  Entertainment Service   
245                   Park             Farmers Market  Entertainment Service   
256      Food & Drink Shop                       Farm             Food Stand   
258        Laundry Service             Ice Cream Shop          Deli / Bodega   
285             Food Court          Food & Drink Shop  Entertainment Service   
303  Entertainment Service       Ethiopian Restaurant          Event Service   
305          Women's Store             Farmers Market   Ethiopian Restaurant   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
27    Ethiopian Restaurant  

In [50]:
# Examine each Cluster for venues in the boroughs of Toronto

# Cluster 1

toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough                                       Neighborhood  \
1          North York                                   Victoria Village   
2    Downtown Toronto                          Regent Park, Harbourfront   
3          North York                   Lawrence Manor, Lawrence Heights   
4    Downtown Toronto        Queen's Park, Ontario Provincial Government   
7          North York                                          Don Mills   
8           East York                    Parkview Hill, Woodbine Gardens   
9    Downtown Toronto                           Garden District, Ryerson   
10         North York                                          Glencairn   
11          Etobicoke  West Deane Park, Princess Gardens, Martin Grov...   
12        Scarborough             Rouge Hill, Port Union, Highland Creek   
13         North York                                          Don Mills   
14          East York                                   Woodbine Heights   
15   Downtown Toronto                                     St. James Town   
16               York                                 Humewood-Cedarvale   
17          Etobicoke  Eringate, Bloordale Gardens, Old Burnhamthorpe...   
18        Scarborough                  Guildwood, Morningside, West Hill   
19       East Toronto                                        The Beaches   
20   Downtown Toronto                                        Berczy Park   
22        Scarborough                                             Woburn   
23          East York                                            Leaside   
24   Downtown Toronto                                 Central Bay Street   
25   Downtown Toronto                                           Christie   
26        Scarborough                                          Cedarbrae   
27         North York                                  Hillcrest Village   
28         North York    Bathurst Manor, Wilson Heights, Downsview North   
29          East York                                   Thorncliffe Park   
30   Downtown Toronto                           Richmond, Adelaide, King   
31       West Toronto                       Dufferin, Dovercourt Village   
33         North York                       Fairview, Henry Farm, Oriole   
34         North York                    Northwood Park, York University   
36   Downtown Toronto  Harbourfront East, Union Station, Toronto Islands   
37       West Toronto                           Little Portugal, Trinity   
38        Scarborough        Kennedy Park, Ionview, East Birchmount Park   
39         North York                                    Bayview Village   
40         North York                                          Downsview   
41       East Toronto                       The Danforth West, Riverdale   
42   Downtown Toronto           Toronto Dominion Centre, Design Exchange   
43       West Toronto       Brockton, Parkdale Village, Exhibition Place   
44        Scarborough                    Golden Mile, Clairlea, Oakridge   
46         North York                                          Downsview   
47       East Toronto                     India Bazaar, The Beaches West   
48   Downtown Toronto                     Commerce Court, Victoria Hotel   
53         North York                                          Downsview   
54       East Toronto                                    Studio District   
55         North York                  Bedford Park, Lawrence Manor East   
56               York   Del Ray, Mount Dennis, Keelsdale and Silverthorn   
58        Scarborough                        Birch Cliff, Cliffside West   
59         North York                                         Willowdale   
60         North York                                          Downsview   
63               York                      Runnymede, The Junction North   
65        Scarborough  Dorset Park, Wexford Heights, Scarborough Town...   
67    Central Toronto                                   Davisv

In [51]:
# Cluster 2

toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough    Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
6  Scarborough  Malvern, Rouge  Fast Food Restaurant         Women's Store   

  3rd Most Common Venue        4th Most Common Venue 5th Most Common Venue  \
6          Dance Studio  Eastern European Restaurant             Drugstore   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6            Donut Shop               Dog Run   Distribution Center   

  9th Most Common Venue 10th Most Common Venue  
6        Discount Store                  Diner

In [52]:
# Cluster 3

toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough                 Neighborhood 1st Most Common Venue  \
32      Scarborough          Scarborough Village            Playground   
83  Central Toronto  Moore Park, Summerhill East            Playground   

   2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue  \
32     Convenience Store         Women's Store                 Dance Studio   
83         Women's Store           Curling Ice  Eastern European Restaurant   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
32  Eastern European Restaurant             Drugstore            Donut Shop   
83                    Drugstore            Donut Shop               Dog Run   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
32               Dog Run   Distribution Center         Discount Store  
83   Distribution Center        Discount Store                  Diner

In [53]:
# Cluster 4

toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough                                       Neighborhood  \
0         North York                                          Parkwoods   
21              York                                Caledonia-Fairbanks   
35         East York                                       East Toronto   
49        North York           North Park, Maple Leaf Park, Upwood Park   
61   Central Toronto                                      Lawrence Park   
64              York                                             Weston   
66        North York                                    York Mills West   
68   Central Toronto                           Forest Hill North & West   
85       Scarborough  Milliken, Agincourt North, Steeles East, L'Amo...   
91  Downtown Toronto                                           Rosedale   
98         Etobicoke      The Kingsway, Montgomery Road, Old Mill North   

   1st Most Common Venue       2nd Most Common Venue 3rd Most Common Venue  \
0               Bus Stop                        Park     Food & Drink Shop   
21                  Park               Women's Store                  Pool   
35                  Park                 Coffee Shop     Convenience Store   
49                  Park  Construction & Landscaping                Bakery   
61                  Park                 Swim School              Bus Line   
64                  Park               Women's Store          Dance Studio   
66                  Park                        Bank     Convenience Store   
68                  Park               Jewelry Store                 Trail   
85                  Park                  Playground                Bakery   
91                  Park                  Playground                 Trail   
98                 River                        Park         Women's Store   

          4th Most Common Venue 5th Most Common Venue  \
0                 Women's Store             Drugstore   
21                  Curling Ice             Drugstore   
35                Women's Store          Dance Studio   
49                Women's Store         Deli / Bodega   
61                 Dance Studio             Drugstore   
64  Eastern European Restaurant             Drugstore   
66                Women's Store         Deli / Bodega   
68             Sushi Restaurant           Curling Ice   
85                  Curling Ice             Drugstore   
91             Cuban Restaurant             Drugstore   
98                    Drugstore            Donut Shop   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                    Donut Shop               Dog Run   Distribution Center   
21                   Donut Shop               Dog Run   Distribution Center   
35  Eastern European Restaurant             Drugstore            Donut Shop   
49  Eastern European Restaurant             Drugstore            Donut Shop   
61                   Donut Shop               Dog Run   Distribution Center   
64                   Donut Shop               Dog Run   Distribution Center   
66  Eastern European Restaurant             Drugstore            Donut Shop   
68                    Drugstore            Donut Shop               Dog Run   
85                   Donut Shop               Dog Run   Distribution Center   
91                   Donut Shop               Dog Run   Distribution Center   
98                      Dog Run   Distribution Center        Discount Store   

   9th Most Common Venue 10th Most Common Venue  
0         Discount Store                  Diner  
21        Discount Store                  Diner  
35               Dog Run    Distribution Center  
49               Dog Run    Distribution Center  
61        Discount Store                  Diner  
64        Discount Store                  Diner  
66               Dog Run    Distribution Center  
68   Distribution Center         Discount Store  
85        Discount Store                  Diner  
91        Discount Store                 

In [54]:
# Cluster 5

toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough             Neighborhood 1st Most Common Venue  \
52       North York  Willowdale, Newtonbrook          Home Service   
62  Central Toronto                 Roselawn                Garden   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
52         Women's Store          Dance Studio     Electronics Store   
62           Music Venue          Home Service         Women's Store   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
52  Eastern European Restaurant             Drugstore            Donut Shop   
62                  Curling Ice             Drugstore            Donut Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
52               Dog Run   Distribution Center         Discount Store  
62               Dog Run   Distribution Center         Discount Store

In [55]:
# Cluster 6

toronto_merged.loc[toronto_merged['Cluster Labels'] == 5, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough      Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
57  North York  Humberlea, Emery        Baseball Field         Women's Store   

   3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
57         Deli / Bodega     Electronics Store  Eastern European Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
57             Drugstore            Donut Shop               Dog Run   

   9th Most Common Venue 10th Most Common Venue  
57   Distribution Center         Discount Store

In [56]:
# Cluster 7

toronto_merged.loc[toronto_merged['Cluster Labels'] == 6, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough   Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
50  North York  Humber Summit            Restaurant           Curling Ice   

          3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
50  Eastern European Restaurant             Drugstore            Donut Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
50               Dog Run   Distribution Center        Discount Store   

   9th Most Common Venue 10th Most Common Venue  
50                 Diner     Dim Sum Restaurant

In [57]:
# Cluster 8

toronto_merged.loc[toronto_merged['Cluster Labels'] == 7, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough              Neighborhood 1st Most Common Venue  \
45  North York  York Mills, Silver Hills             Cafeteria   

   2nd Most Common Venue 3rd Most Common Venue        4th Most Common Venue  \
45         Women's Store          Dance Studio  Eastern European Restaurant   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
45             Drugstore            Donut Shop               Dog Run   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
45   Distribution Center        Discount Store                  Diner

In [58]:
# Cluster 9

toronto_merged.loc[toronto_merged['Cluster Labels'] == 8, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough                                     Neighborhood  \
51  Scarborough  Cliffside, Cliffcrest, Scarborough Village West   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
51   American Restaurant                 Motel         Women's Store   

   4th Most Common Venue        5th Most Common Venue 6th Most Common Venue  \
51          Dance Studio  Eastern European Restaurant             Drugstore   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
51            Donut Shop               Dog Run   Distribution Center   

   10th Most Common Venue  
51         Discount Store

In [59]:
# Cluster 10

toronto_merged.loc[toronto_merged['Cluster Labels'] == 9, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
94  Etobicoke    Northwest             Drugstore   Rental Car Location   

   3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
94         Women's Store           Curling Ice  Eastern European Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
94            Donut Shop               Dog Run   Distribution Center   

   9th Most Common Venue 10th Most Common Venue  
94        Discount Store                  Diner

In [60]:
# Examine neighborhoods in Cluster 4 of Toronto
# It has "Parks" as the most common venue

# Cluster 4

toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[0] + [1] + list(range(5, toronto_merged.shape[1]))]]

Borough                                       Neighborhood  \
0         North York                                          Parkwoods   
21              York                                Caledonia-Fairbanks   
35         East York                                       East Toronto   
49        North York           North Park, Maple Leaf Park, Upwood Park   
61   Central Toronto                                      Lawrence Park   
64              York                                             Weston   
66        North York                                    York Mills West   
68   Central Toronto                           Forest Hill North & West   
85       Scarborough  Milliken, Agincourt North, Steeles East, L'Amo...   
91  Downtown Toronto                                           Rosedale   
98         Etobicoke      The Kingsway, Montgomery Road, Old Mill North   

   1st Most Common Venue       2nd Most Common Venue 3rd Most Common Venue  \
0               Bus Stop                        Park     Food & Drink Shop   
21                  Park               Women's Store                  Pool   
35                  Park                 Coffee Shop     Convenience Store   
49                  Park  Construction & Landscaping                Bakery   
61                  Park                 Swim School              Bus Line   
64                  Park               Women's Store          Dance Studio   
66                  Park                        Bank     Convenience Store   
68                  Park               Jewelry Store                 Trail   
85                  Park                  Playground                Bakery   
91                  Park                  Playground                 Trail   
98                 River                        Park         Women's Store   

          4th Most Common Venue 5th Most Common Venue  \
0                 Women's Store             Drugstore   
21                  Curling Ice             Drugstore   
35                Women's Store          Dance Studio   
49                Women's Store         Deli / Bodega   
61                 Dance Studio             Drugstore   
64  Eastern European Restaurant             Drugstore   
66                Women's Store         Deli / Bodega   
68             Sushi Restaurant           Curling Ice   
85                  Curling Ice             Drugstore   
91             Cuban Restaurant             Drugstore   
98                    Drugstore            Donut Shop   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                    Donut Shop               Dog Run   Distribution Center   
21                   Donut Shop               Dog Run   Distribution Center   
35  Eastern European Restaurant             Drugstore            Donut Shop   
49  Eastern European Restaurant             Drugstore            Donut Shop   
61                   Donut Shop               Dog Run   Distribution Center   
64                   Donut Shop               Dog Run   Distribution Center   
66  Eastern European Restaurant             Drugstore            Donut Shop   
68                    Drugstore            Donut Shop               Dog Run   
85                   Donut Shop               Dog Run   Distribution Center   
91                   Donut Shop               Dog Run   Distribution Center   
98                      Dog Run   Distribution Center        Discount Store   

   9th Most Common Venue 10th Most Common Venue  
0         Discount Store                  Diner  
21        Discount Store                  Diner  
35               Dog Run    Distribution Center  
49               Dog Run    Distribution Center  
61        Discount Store                  Diner  
64        Discount Store                  Diner  
66               Dog Run    Distribution Center  
68   Distribution Center         Discount Store  
85        Discount Store                  Diner  
91        Discount Store                 

In [61]:
# Examine neighborhoods in Cluster 9 of New York City
# It has "Parks" as the most common venue

# Cluster 9

new_york_merged.loc[new_york_merged['Cluster Labels'] == 8, new_york_merged.columns[[0] + [1] + list(range(5, new_york_merged.shape[1]))]]

Borough Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
192         Queens   Somerville                  Park         Women's Store   
203  Staten Island    Todt Hill                  Park         Women's Store   

    3rd Most Common Venue  4th Most Common Venue 5th Most Common Venue  \
192             Irish Pub  Entertainment Service  Ethiopian Restaurant   
203             Irish Pub  Entertainment Service  Ethiopian Restaurant   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
192         Event Service           Event Space               Exhibit   
203         Event Service           Event Space               Exhibit   

    9th Most Common Venue 10th Most Common Venue  
192               Factory     Falafel Restaurant  
203               Factory     Falafel Restaurant

In [62]:
print('New York City has {} boroughs and {} neighborhoods.'.format(
        len(new_york_merged['Borough'].unique()), len(new_york_merged['Neighborhood'].unique())
    )
)

New York City has 5 boroughs and 300 neighborhoods.


In [63]:
print('Toronto has {} boroughs and {} neighborhoods.'.format(
        len(toronto_merged['Borough'].unique()), len(toronto_merged['Neighborhood'].unique())
    )
)

Toronto has 10 boroughs and 96 neighborhoods.
